# Гомологичное моделирование комплекса белка с лигандом

In [22]:
import sys 
import modeller 
import _modeller
import modeller.automodel 

In [23]:
env=modeller.environ()
env.io.hetatm=True

In [26]:
! wget http://www.pdb.org/pdb/files/1lmp.pdb

--2021-05-27 22:11:41--  http://www.pdb.org/pdb/files/1lmp.pdb
Resolving www.pdb.org (www.pdb.org)... 128.6.159.96
Connecting to www.pdb.org (www.pdb.org)|128.6.159.96|:80... connected.
HTTP request sent, awaiting response... 301 Moved Permanently
Location: https://www.rcsb.org/pdb/files/1lmp.pdb [following]
--2021-05-27 22:11:41--  https://www.rcsb.org/pdb/files/1lmp.pdb
Resolving www.rcsb.org (www.rcsb.org)... 128.6.159.248
Connecting to www.rcsb.org (www.rcsb.org)|128.6.159.248|:443... connected.
HTTP request sent, awaiting response... 301 Moved Permanently
Location: https://files.rcsb.org/download/1lmp.pdb [following]
--2021-05-27 22:11:42--  https://files.rcsb.org/download/1lmp.pdb
Resolving files.rcsb.org (files.rcsb.org)... 128.6.158.49
Connecting to files.rcsb.org (files.rcsb.org)|128.6.158.49|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: unspecified [application/octet-stream]
Saving to: `1lmp.pdb.1'

    [  <=>                                  ] 128

In [27]:
! wget http://www.uniprot.org/uniprot/P50718.fasta

--2021-05-27 22:11:51--  http://www.uniprot.org/uniprot/P50718.fasta
Resolving www.uniprot.org (www.uniprot.org)... 128.175.240.206, 193.62.193.81
Connecting to www.uniprot.org (www.uniprot.org)|128.175.240.206|:80... connected.
HTTP request sent, awaiting response... 301 Moved Permanently
Location: https://www.uniprot.org/uniprot/P50718.fasta [following]
--2021-05-27 22:11:51--  https://www.uniprot.org/uniprot/P50718.fasta
Connecting to www.uniprot.org (www.uniprot.org)|128.175.240.206|:443... connected.
HTTP request sent, awaiting response... 200 
Length: 211 [text/plain]
Saving to: `P50718.fasta'

100%[======================================>] 211         --.-K/s   in 0s      

2021-05-27 22:11:53 (87.3 MB/s) - `P50718.fasta' saved [211/211]



In [28]:
alignm=modeller.alignment(env)

In [29]:
alignm.append(file='P50718.fasta', align_codes='all',alignment_format='FASTA')
## создадим модель
mdl = modeller.model(env, file='1lmp.pdb', model_segment=('FIRST:'+'A', 'LAST:'+'A'))
## и добавим в выравнивание
alignm.append_model(mdl, atom_files='1lmp.pdb', align_codes='1lmp')
## добавим идентификаторы
alignm[0].code = 'TRINI'
alignm[1].code = 'source'

In [19]:
#посмотрим на получившееся выравнивание
! cat all_in_one.ali


>P1;ENLYS_BPT5
sequence::     : :     : :::-1.00:-1.00
MSFKFGKNSEKQLATVKPELQKVARRALELSPYDFTIVQGIRTVAQSAQNIANGTSFLKDPSKSKHITGDAIDFA
PYINGKIDWNDLEAFWAVKKAFEQAGKELGIKLRFGADWNASGDYHDEIKRGTYDGGHVELV*

>P1;1lmp
sequence::     : :     : :::-1.00:-1.00
MSFKFGKNSEKQLATVKPELQKVARRALELSPYDFTIVQGIRTVAQSAQNIANGTSFLKDPSKSKHITGDAIDFA
PYINGKIDWNDLEAFWAVKKAFEQAGKELGIKLRFGADWNASGDYHDEIKRGTYDGGHVELV*

>P1;1lmp
structureX:1lmp.pdb:   1 :A:+129 :A:MOL_ID  1; MOLECULE  LYSOZYME; CHAIN  A; SYNONYM  MUCOPEPTIDE N-ACETYLMURAMYLHYDROLASE; EC  3.2.1.17:MOL_ID  1; ORGANISM_SCIENTIFIC  ONCORHYNCHUS MYKISS; ORGANISM_COMMON  RAINBOW TROUT; ORGANISM_TAXID  8022; ORGAN  KIDNEY: 2.00: 0.16
---KVYDRCELARALKASGMDGYAGNSLPNWVCLSKWESSYNTQATNRNTDGSTDYGIFQINSRYWCDDGRTPGA
KNVCGIRCSQLLTDDLTVAIRCAKRVVLDPNGIGAWVAWRLHCQNQDLRSYVAGCG-----V*


In [30]:
alignm.salign()
alignm.write(file='all_in_one.ali', alignment_format='PIR')


SALIGN_____> adding the next group to the alignment; iteration    1


In [31]:
! cat all_in_one.ali


>P1;TRINI
sequence::     : :     : :::-1.00:-1.00
MQKLRVFLLALAALCISCEAKYFATNCELVHELRRQGFPEDKMRDWVCLIQNESGRNTSKMGTINKNGSRDYGLF
QINDKYWCSKTSTPGKD--CNVTCAEMLLDDITKASKCAKKI-YKRHKFQAWYGWRNHCQG----TLPDISKC*

>P1;source
structureX:1lmp.pdb:   1 :A:+129 :A:MOL_ID  1; MOLECULE  LYSOZYME; CHAIN  A; SYNONYM  MUCOPEPTIDE N-ACETYLMURAMYLHYDROLASE; EC  3.2.1.17:MOL_ID  1; ORGANISM_SCIENTIFIC  ONCORHYNCHUS MYKISS; ORGANISM_COMMON  RAINBOW TROUT; ORGANISM_TAXID  8022; ORGAN  KIDNEY: 2.00: 0.16
KVYDRCELA------------------RALKASGMDGYAGNSLPNWVCLSKWESSYNTQATNR-NTDGSTDYGIF
QINSRYWCDDGRTPGAKNVCGIRCSQLLTDDLTVAIRCAKRVVLDPNGIGAWVAWRLHCQNQDLRSYVAGCGV*


In [32]:
## Выбираем объект для моделирования 
s = alignm[0]
pdb = alignm[1]

print(s.code, pdb.code)

## Создаем объект automodel
a = modeller.automodel.automodel(env, alnfile='all_in_one.ali', knowns=pdb.code, sequence=s.code)

a.name='mod'+s.code
a.starting_model = 1
a.ending_model = 2
a.make()

TRINI source

check_ali___> Checking the sequence-structure alignment. 

Implied intrachain target CA(i)-CA(i+1) distances longer than  8.0 angstroms:

ALN_POS  TMPL  RID1  RID2  NAM1  NAM2     DIST
----------------------------------------------
     92     1   73    76      D     C    8.895
    136     1  117   122      G     T   13.814
END OF TABLE
read_to_681_> topology.submodel read from topology file:        3
patch_s_522_> Number of disulfides patched in MODEL:        3
mdtrsr__446W> A potential that relies on one protein is used, yet you have at
              least one known structure available. MDT, not library, potential is used.
0 atoms in HETATM/BLK residues constrained
to protein atoms within 2.30 angstroms
and protein CA atoms within 10.00 angstroms
0 atoms in residues without defined topology
constrained to be rigid bodies
condens_443_> Restraints marked for deletion were removed.
              Total number of restraints before, now:    11741    10737
iupac_m_397W> Atoms 



>> ENERGY; Differences between the model's features and restraints:
Number of all residues in MODEL                   :      141
Number of all, selected real atoms                :     1135    1135
Number of all, selected pseudo atoms              :        0       0
Number of all static, selected restraints         :    10737   10737
COVALENT_CYS                                      :        F
NONBONDED_SEL_ATOMS                               :        1
Number of non-bonded pairs (excluding 1-2,1-3,1-4):     2396
Dynamic pairs routine                             : 2, NATM x NATM cell sorting
Atomic shift for contacts update (UPDATE_DYNAMIC) :    0.390
LENNARD_JONES_SWITCH                              :    6.500   7.500
COULOMB_JONES_SWITCH                              :    6.500   7.500
RESIDUE_SPAN_RANGE                                :        0   99999
NLOGN_USE                                         :       15
CONTACT_SHELL                                     :    4.000
DYNAMIC_P

In [33]:
from IPython.display import display, Image

In [ ]:
import __main__
__main__.pymol_argv = [ 'pymol', '-x' ]

import pymol
pymol.finish_launching()
from pymol import cmd, stored

In [1]:
cmd.load('TRINI.B99990001.pdb', 'model1')
cmd.load('1lmp.pdb', 'source')
cmd.do('align model1, source')
cmd.do('remove hetatm')
cmd.bg_color('white')
cmd.set('ray_trace_mode', 3)

NameError: name 'cmd' is not defined